In [1]:
import numpy as np

Problem 1:

The pseudocode:
- two helper functions: one that gets the reverse compliment, and one that takes a DNA sequence and returns a list with 3-letter codon chunks
- a primary function that actually calculates long ORF coverage
> Since long ORFs are defined to be $\geq$ 200 bp in length, we will count all the long ORFs we can find and then "take the ratio of the total length of long ORFs in all six frames, over the total length of the genome"
 

In [2]:
#function that takes in a DNA sequence and calculates what percentage of the sequence is an ORF
#  note that the output is in the range of [0,6] since we are parsing 6 reading frames, and each
#  reading frame maximally contributes 1 to the total (this would be the case where the entire sequence is an ORF)
def getORFCoverage(seq, noncanonicalStops = None):
    #every time we find a long ORF, we will add its length to this variable
    totalLongORFCount = 0

    #for problem 5, we need to consider different sets of stop codons. We introduce a third parameter that, if left empty, 
    #  will use the canonical set of stopCodons
    if (noncanonicalStops != None):
        stopCodons = noncanonicalStops
    else:
        stopCodons = ["TAA","TAG","TGA"]

    #we will call our helper function to get codons in our specified frame
    codons = []
    for frames in range(3):
        # three reading frames for the forward strand
        codons.append(getCodons(seq,frames))
        # three reading frames for the reverse strand
        codons.append(getCodons(getReverseCompliment(seq), frames))

    #this loops counts number of long ORFs in the forward coding sequence; we repeat this loop separately for the reverse strand
    #  (even though its kind of gross coding) so that we don't miss edge cases
    for readingFrame in codons:

        # we will use this variable to count how many codons we've encountered since our last stop codon
        currentORFLength = 0
        for codon in readingFrame:

            #for every codon we encounter, we'll keep adding to our running total
            #  because 'An "open reading frame" is any sequence of triplets free of stop codons'
            currentORFLength += 1

            # if we encounter any of the given stop codons (which we stored in stopCodons), then we stop counting
            for stops in stopCodons:
                if (codon == stops):
            
                    #subtract 1 because stop codons should not be counted in ORF length
                    currentORFLength -= 1
    
                    #only consider it a long ORF if it is longer than 200 bp
                    if (currentORFLength >= 200): 
                        
                        #multiply by 3 because currentORFLength counts codons, not base pairs
                        totalLongORFCount += (3 * currentORFLength)

                    #since we encountered a stop, we're resetting our reading frame
                    currentORFLength = 0

        #this if statement only happens after we have iterated through every codon
        #  if there is a reading frame that never ended, then we ask if it is a long reading frame (>= 200 bp)
        if (currentORFLength >= 200):
            totalLongORFCount += 3 * currentORFLength
    
    return (totalLongORFCount / len(seq))
                
        
#helper function to generate the reverse strand. Remember that it is the reverse complement
#  Pseudocode: We will generate the reverse strand and then iterate through char by char, taking the reverse compliment of each bp 
#  and adding it to a string that we return at the end
def getReverseCompliment(seq):
    #slicing backwards, we store the reverse of seq in rev
    rev = seq[::-1]

    #as we generate the reverse compliment, we will add the base pairs to this variable
    newSeq = ""

    #TODO: should we account for non-ATCG letters?
    
    #now, we generate the reverse compliment 
    for i in range(len(rev)):
        if (rev[i] == "A"):
            newSeq = newSeq + "T"
        if (rev[i] == "T"):
            newSeq = newSeq + "A"
        if (rev[i] == "C"):
            newSeq = newSeq + "G"
        if (rev[i] == "G"):
            newSeq = newSeq + "C"
    
    return newSeq

#helper function to get base pair triplets from a given sequence and a given frame (integer)
def getCodons(seq, frame):
    
    #note that frame % 3 = 0 means no offset, frame % 3 = 1 means offset by 1 bp, and frame % 3 = 2 means offset by 2 bp
    frameShift = frame % 3
    
    #we will store the codons we find in a list
    codons = []

    #if the sequence is not a multiple of 3 in length after adjusting for frame, then we will ignore the last however many 
    #  characters of junk code
    junkLen = (len(seq) - (frameShift)) % 3

    #this loop accounts for the frameShift and the junkLen at the end of the sequence
    for i in range(0 + frameShift,len(seq) - frameShift - junkLen, 3):
        codons.append(seq[i:i+3])
    return codons
        

        

In [3]:
#Code block to test the above helper functions 

str = "THECATHADTHEBIGHAT"
#this loop should print "THE" "CAT" "HAD" "THE" "BIG" "HAT"
for triplets in getCodons(str,0):
    print(triplets)
print('\n')
#this loop should print "HEC" "ATH" "ADT" "HEB" "IGH" and not print the last two letters "AT"
for triplets in getCodons(str,4):
    print(triplets)
print('\n')
str = "ATGCCAGGT"
print(getReverseCompliment(str))


THE
CAT
HAD
THE
BIG
HAT


HEC
ATH
ADT
HEB
IGH


ACCTGGCAT


In [4]:
#block of code to test getORFCoverage

#5 codons in +2 shift frame
# 10 codons in +0 shift frame
rSeq = "ATGCCCAAATGTTCCCGGGAAATTTTTGACCGGTAG" #note that this line doesn't really work since we have 200 bp as our ORF cutoff; edit that number and it should work again
rseq2 = "CCC" * 400
print(getORFCoverage(rSeq))
print(len(rSeq))

print(getORFCoverage(rseq2))


0.0
36
5.99


Problem 2:

The pseudocode:
- we will create an initial array with a fixed number of G/C's and A/T's based on the given GC content, a value passed to the function as a parameter
> we rely on rng.random to determine the specific ratio of G's to C's
- then we will shuffle the initial array using np.random.shuffle()

In [5]:
#the parameters are such: 
#  - length is the desired length of our final synthetic sequence
#  - GCComposition is in the range [0,1] and tells us what fraction of our sequence should be GC
#    - We will use floor(length * CGComposition) as our number of CG base pairs in our sequence; we round to the closest integer
def getSyntheticSeq(length, GCComposition):
    #instantiate rng object from numpy
    rng = np.random.default_rng()
    
    #we first generate an array with a given GC/AT composition; note that AT% = 1 - CG%
    syntheticSeq = np.array([])
    CGCount = int(np.round(length * GCComposition))

    #to generate CGCount-many C's and G's, we will randomly pick C or G with equal probability; we let rng.choice() handle this
    CGArray = rng.choice(["C","G"], size = CGCount, p = [0.5,0.5])
    
    #we concatenate CGarray to syntheticSeq so that we have CGCount-many C's and G's in our synthetic sequence
    #  concatenate is how we are supposed to combine various np.arrays!
    syntheticSeq = np.concatenate((syntheticSeq, CGArray))

    #repeat the above process for A's and T's
    ATArray = rng.choice(["T","A"], size = length - CGCount, p = [0.5,0.5])
    syntheticSeq = np.concatenate((syntheticSeq, ATArray))

    #np.random.shuffle() takes an np.array as an argument and randomly shuffles it
    np.random.shuffle(syntheticSeq)

    #since we want the sequence to be a string, we first convert the np.array to a list, and then convert the list to a string
    return ''.join(syntheticSeq.tolist())
    

The block of code below calculates the ORF coverage for varying GC content. 
- let's generate sequences of 10000 bp in length using getSyntheticSeq(), with varying GC content ranging from 0 to 1
- let's generate 100 different sequences at each GC percentage (and average at the end) so that we have more statistical power 

In [6]:
# For a given GC composition, we will find the average long ORF coverage over 100 trials and then store it in this creatively named list
arr = []

# GC content will range from 0 to 100 with increments of 5%
for GCpercentage in range(0,105,5):
    #val will be a running sum for long ORF coverage at a given GC content
    val = 0
    trials = 100
    for i in range(trials):
        syntheticSeq = getSyntheticSeq(10000, GCpercentage/100)
        val += getORFCoverage(syntheticSeq)

    arr.append(val/trials)

print("GC composition \t ORF Coverage")
for i in range(len(arr)):
    print(i * 5, "\t \t ", format(arr[i], ".2f"))

GC composition 	 ORF Coverage
0 	 	  0.00
5 	 	  0.00
10 	 	  0.00
15 	 	  0.00
20 	 	  0.00
25 	 	  0.00
30 	 	  0.00
35 	 	  0.00
40 	 	  0.00
45 	 	  0.00
50 	 	  0.00
55 	 	  0.01
60 	 	  0.06
65 	 	  0.23
70 	 	  0.54
75 	 	  1.34
80 	 	  2.60
85 	 	  4.20
90 	 	  5.39
95 	 	  5.92
100 	 	  6.00


In [7]:
#another block of code to see which value between 55 and 60% GC composition yield 0.05 coverage
arr = []

# GC content will range from 0 to 100 with increments of 5%
for GCpercentage in range(50,60,1):
    #val will be a running sum for long ORF coverage at a given GC content
    val = 0
    trials = 100
    for i in range(trials):
        syntheticSeq = getSyntheticSeq(10000, GCpercentage/100)
        val += getORFCoverage(syntheticSeq)

    arr.append(val/trials)

print("GC composition \t ORF Coverage")
for i in range(len(arr)):
    print(i + 50, "\t \t ", format(arr[i], ".2f"))

GC composition 	 ORF Coverage
50 	 	  0.00
51 	 	  0.00
52 	 	  0.01
53 	 	  0.01
54 	 	  0.01
55 	 	  0.02
56 	 	  0.02
57 	 	  0.03
58 	 	  0.03
59 	 	  0.05


**Answering Question 2** 

Note that literally anything can be chosen as the threshold for statistical significance; however, we will abide by the common 0.05 threshold.

We argue that some value around 59% GC composition is sufficient to assume that long ORFs ($\geq$ 200 bp) is statistically significant. If we have a genome with less than 59% GC content, we can expect that our false positive rate on calling protein-coding regions is less than 5%––this is because, in a randomly generated sequence with 59% gc content, simulations show that 5% of the sequence is covered by long ORFs, despite the fact that a randomly generated sequence does not contain any real protein-coding regions.

I don't believe my code, so let's do some (not) back of the envelope calculations to imagine how many ORFs we can expect in a sequence of 10,000 bp with GC percentage $k$. Let us assume that the probability of having a cystosine or guanine is $\frac{k}{2}$ and the probability of adenosine or thymine is $\frac{1 - k}{2}$

The probability that we have a stop codon, TAA or TAG or TGA, is going to be $\frac{(1-k)^{3}}{8}, \frac{(1 - k)^{2}(k)}{8},$ and $\frac{(1 - k)^{2}(k)}{8}$  respectively. Collectively, the chance that any codon is a stop codon is going to be the sum of these three, $\frac{(1-k)^{3} + 2(1 - k)^{2}(k)}{8}$

To find a long ORF, we need to encounter at least 200 non-stop codons, with each non-stop codon occuring with probability $1 - \frac{(1-k)^{3} + 2(1 - k)^{2}(k)}{8}$

hence p(long ORF) = $\sum_{n = 200}^{\infty} (1 - \frac{(1-k)^{3} + 2(1 - k)^{2}(k)}{8})^{n}$ which is a (converging) geometric series that we should be able to find a closed form of using the formula $\frac{a_{1}}{1-r}$ where $a_{1} = \left( 1 - \frac{(1-k)^{3} + 2(1 - k)^{2}(k)}{8}\right)^{200}$ and $r = 1 - \frac{(1-k)^{3} + 2(1 - k)^{2}(k)}{8}$.

For $k = 0.59$, we get an answer around $\frac{a}{1-r} = \frac{0.0011}{1-0.966} = 0.03$ ORF coverage; so our code is at least in the right(ish) ball park for calculating ORF coverage.

Problem 3: Getting TAR files
- uhhh, I guess I just did it? 

Problem 4: 

The pseudocode:
- we will delete everything before the first '\n' character, since this should all be header, and then we will delete all remaining '\n' characters

In [8]:
def readFASTA(file):
    #open the file and then store it in a variable
    with open(file, 'r') as FASTAFile:
        fileContent = FASTAFile.read()

        #we will delete everything before the first '\n' character, since this should all be header, and then we will delete all remaining '\n' characters
        #make a copy of fileContent cause I'm scared of irreversably manipulating strings
        copy = fileContent
        copy = copy[copy.find('\n'):len(copy)]
        copy = copy.replace('\n', '')
        
        return copy

Problem 5: 

Pseudo code:
- store the names of all 10 fasta files in a list
- run this code three times for the different sets of stop codons

In [9]:
#genomes stores the name of the 10 phage genome files
genomes = ["phage-genomes/arugula.fa", "phage-genomes/basil.fa", "phage-genomes/chickpea.fa", "phage-genomes/gooseberry.fa", "phage-genomes/huckleberry.fa", "phage-genomes/juniper.fa", "phage-genomes/lentil.fa", "phage-genomes/quince.fa", "phage-genomes/sage.fa","phage-genomes/tangerine.fa"]

#we will parse each FASTA file and then add it to phageGenomes
phageGenomes = []
for genome in genomes:
    phageGenomes.append(readFASTA(genome))

In [10]:
#We will store all three sets of stop codons we are testing on
stopCodons = [["TAA","TAG","TGA"], ["TAA","TGA"], ["TAA", "TAG"]]

print("genome \t \t \t \t stop codons \t\t coverage ")
for i in range(len(phageGenomes)):
    for set in stopCodons:
        print( genomes[i], "\t ", set, "\t", getORFCoverage(phageGenomes[i], set))
    print('\n')
    

genome 	 	 	 	 stop codons 		 coverage 
phage-genomes/arugula.fa 	  ['TAA', 'TAG', 'TGA'] 	 0.372687467045689
phage-genomes/arugula.fa 	  ['TAA', 'TGA'] 	 0.3953485706425804
phage-genomes/arugula.fa 	  ['TAA', 'TAG'] 	 0.7367265766488618


phage-genomes/basil.fa 	  ['TAA', 'TAG', 'TGA'] 	 0.7795152062014232
phage-genomes/basil.fa 	  ['TAA', 'TGA'] 	 0.8537723273793655
phage-genomes/basil.fa 	  ['TAA', 'TAG'] 	 0.8565715809117569


phage-genomes/chickpea.fa 	  ['TAA', 'TAG', 'TGA'] 	 0.8421917005763779
phage-genomes/chickpea.fa 	  ['TAA', 'TGA'] 	 0.8829565781352972
phage-genomes/chickpea.fa 	  ['TAA', 'TAG'] 	 0.9188886680544368


phage-genomes/gooseberry.fa 	  ['TAA', 'TAG', 'TGA'] 	 0.28897271690499166
phage-genomes/gooseberry.fa 	  ['TAA', 'TGA'] 	 0.7761499546743866
phage-genomes/gooseberry.fa 	  ['TAA', 'TAG'] 	 0.38658361844606254


phage-genomes/huckleberry.fa 	  ['TAA', 'TAG', 'TGA'] 	 0.797650567905504
phage-genomes/huckleberry.fa 	  ['TAA', 'TGA'] 	 0.8602228394194503
phage-g

We argue that the TAG recoded genomes are: **juniper.fa and goosberry.fa**
- because ORF coverage is much higher when TAG is recoded, indiciating that we were falsely considering them not ORFs
  
We argue that the TGA recode genomes are: **lentil.fa and arugula.fa**

In [11]:

%load_ext watermark 
%watermark -v -m -p numpy,matplotlib,seaborn,pandas,jupyterlab

Python implementation: CPython
Python version       : 3.12.5
IPython version      : 8.27.0

numpy     : 2.1.1
matplotlib: 3.9.2
seaborn   : 0.13.2
pandas    : 2.2.2
jupyterlab: 4.2.5

Compiler    : Clang 16.0.6 
OS          : Darwin
Release     : 21.6.0
Machine     : arm64
Processor   : arm
CPU cores   : 8
Architecture: 64bit

